In [1]:
import pickle

In [2]:
with open("experiments/inferencing/input_output_train_7b", 'rb') as f:
    outputs_7b = pickle.load(f)

In [3]:
with open("experiments/inferencing/input_output_train_13b", 'rb') as f:
    outputs_13b = pickle.load(f)

In [4]:
with open("experiments/inferencing/input_output_train_tiny", 'rb') as f:
    outputs_tiny = pickle.load(f)

In [5]:
print(f"Length of outputs_7b['cnn_dailymail']: {len(outputs_7b['cnn_dailymail'])}")
print(f"Length of outputs_13b['cnn_dailymail']: {len(outputs_13b['cnn_dailymail'])}")
print(f"Length of outputs_tiny['cnn_dailymail']: {len(outputs_tiny['cnn_dailymail'])}")

Length of outputs_7b['cnn_dailymail']: 3000
Length of outputs_13b['cnn_dailymail']: 3000
Length of outputs_tiny['cnn_dailymail']: 3000


In [6]:
outputs_13b['cnn_dailymail'] = outputs_13b['cnn_dailymail'][:3000]

print(f"Length of outputs_tiny['cnn_dailymail'] after slicing: {len(outputs_tiny['cnn_dailymail'])}")

Length of outputs_tiny['cnn_dailymail'] after slicing: 3000


In [7]:
with open('experiments/inferencing/input_output_train_13b', 'wb') as f:
    pickle.dump(outputs_13b, f)

In [8]:
len(outputs_7b["cnn_dailymail"])

3000

In [9]:
combined_outputs = {}

for dataset_key in outputs_7b.keys():
    combined_outputs[dataset_key] = []

    for i in range(len(outputs_7b[dataset_key])):
        combined_entry = {
            "input_text": outputs_7b[dataset_key][i]["input_text"],  
            "7b": outputs_7b[dataset_key][i].get("7b"),     
            "13b": outputs_13b[dataset_key][i].get("13b"),
            "tiny": outputs_tiny[dataset_key][i].get("tiny")         
        }
        combined_outputs[dataset_key].append(combined_entry)

with open("data/input_output_train", 'wb') as f:
    pickle.dump(combined_outputs, f)

In [10]:
len(combined_outputs["wmt14"])

3000

In [11]:
len(combined_outputs["cnn_dailymail"])

3000

In [13]:
from datasets import load_dataset
import pickle

wmt14_dataset = load_dataset('wmt14', 'de-en', split='test')
cnndailymail_dataset = load_dataset('abisee/cnn_dailymail', '2.0.0', split='test')

def match_labels(combined_outputs, wmt14_dataset, cnndailymail_dataset):
    # Match wmt14 dataset
    if 'wmt14' in combined_outputs:
        for i, entry in enumerate(combined_outputs['wmt14']):
            if i < len(wmt14_dataset):
                entry['label'] = wmt14_dataset[i]['translation']['en'] 

    if 'cnn_dailymail' in combined_outputs:
        for i, entry in enumerate(combined_outputs['cnn_dailymail']):
            if i < len(cnndailymail_dataset):
                entry['label'] = cnndailymail_dataset[i]['highlights']  

    return combined_outputs

with open("data/input_output_train", 'rb') as f:
    combined_outputs = pickle.load(f)

combined_outputs = match_labels(combined_outputs, wmt14_dataset, cnndailymail_dataset)

with open("data/input_output_train", 'wb') as f:
    pickle.dump(combined_outputs, f)

print("Updated combined_outputs saved with labels.")

Updated combined_outputs saved with labels.


In [14]:
combined_outputs["cnn_dailymail"]

[{'input_text': '(CNN)The Palestinian Authority officially became the 123rd member of the International Criminal Court on Wednesday, a step that gives the court jurisdiction over alleged crimes in Palestinian territories. The formal accession was marked with a ceremony at The Hague, in the Netherlands, where the court is based. The Palestinians signed the ICC\'s founding Rome Statute in January, when they also accepted its jurisdiction over alleged crimes committed "in the occupied Palestinian territory, including East Jerusalem, since June 13, 2014." Later that month, the ICC opened a preliminary examination into the situation in Palestinian territories, paving the way for possible war crimes investigations against Israelis. As members of the court, Palestinians may be subject to counter-charges as well. Israel and the United States, neither of which is an ICC member, opposed the Palestinians\' efforts to join the body. But Palestinian Foreign Minister Riad al-Malki, speaking at Wedne